In [1]:
import pandas as pd
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt
plt.style.use("seaborn-notebook")

from ipywidgets import interact, interactive, fixed
import ipywidgets as widgets
from IPython.display import display

import notes_tools.tools as tools
from notes_tools.generate_bilan import texenv
from notes_tools.tools.df_marks_manip import round_half_point

In [2]:
classe = "509"

In [3]:
ws = tools.get_class_ws(classe)
flat = tools.extract_flat_marks(ws)

In [4]:
quest_pov, exo_pov, eval_pov = tools.digest_flat_df(flat)

Création des bilans trimestriels

In [5]:
def create_summary_table(pv_table, coefs = ""):
    if coefs:
        cols = [("Evaluations",["Note", "Note sur 20", "Coefficient"])]
    else:
        cols = [("Evaluations",["Note", "Note sur 20"])]
    for k,v in pv_table.iterrows():
        if coefs:
            cols.append((k[1], ["{}/{}".format(v.iloc[1], v.iloc[0]), "", coefs[k[1]]]))
        else:
            cols.append((k[1], ["{}/{}".format(v.iloc[1], v.iloc[0]), ""]))
            #cols[k[1]] = ["{}/{}".format(v.iloc[1], v.iloc[0]), ""]
    #df = pd.DataFrame.from_dict(cols)
    df = pd.DataFrame.from_items(cols)
    #return df.set_index('Evaluations')
    return df

In [6]:
def build_latex_content(eval_pov, coefs=""):
    table = pd.pivot_table(eval_pov,
              index = ["Eleve", "Nom"],
              values = ["Mark", "Bareme"],
              #columns = ["Nom"],
              )
    content = {}
    content["students"] = []
    for e in eval_pov["Eleve"].unique():
        eleve = {"name":e}
        e_table = table.query('Eleve == "{}"'.format(e))
        summary = create_summary_table(e_table, coefs)
        
        col_format = "|"+"c|"*len(summary.columns)
        #print(len(summary.columns))
        eleve['latex_table'] = summary.to_latex(index=False, column_format=col_format)
        content["students"].append(eleve)
    return content

In [7]:
coefs = {"DM1":0.5, "DM2":0.5, "DS1":1, "DS2":1, "ConnT1":1}

In [8]:
#build_latex_content(eval_pov)

In [9]:
#content = build_latex_content(eval_pov, coefs)
content = build_latex_content(eval_pov)
tpl = texenv.get_template("./tpl_bilan_trim.tex")
with open("./{}/trim1.tex".format(classe), "w")  as f:
    f.write(tpl.render(content))